# Mérnöki modellalkotás vizsga
**Optikai hiba lokalizálás**

_Torma Kristóf	Y8O353_
## Feladat
Adjon meg egy olyan bináris mátrixot, amelyiknek kevesebb oszlopa van, mint sora, és bármely legfeljebb 2 sor (bitenkénti) VAGY vektora egyedi. (Nem triviális 2-separable hibakód) Válaszodat indokold, és mondj olyan link hibákat, amelyeket a fenti m-trail mátrixszal azonosítani tudunk!
## Megoldás
A feladat megoldását a sorok és oszlopok számának meghatározásával kezdtem. A következő kifejezésekben a mátrix oszlopainak számát ```n```-nel jelöltem.
### Előkészületek
Mivel a bitenkénti ```VAGY``` műveletet minden sor esetében elvégezzük önmagán, ezért ```n+1``` sorú mátrix esetében legalább ```n+1``` vektort állítunk össze. Emellett mindegyik sorát a mátrixnak bitenként ```VAGY```-olunk minden másik sorával. Ez
\begin{equation*}
\frac{\ n\ast\left(n+1\right)}{2}
\end{equation*}
darab vektort jelent. Tehát összesen
\begin{equation*}
\frac{\ n\ast\left(n+1\right)}{2}\ +\ n\ +\ 1
\end{equation*}
darabszámú vektor fog keletkezni.
Triviális, hogy a keletkezett vektorok egyediségének szükséges feltétele az
\begin{equation*}
\frac{\ n\ast\left(n+1\right)}{2}\ +\ n\ +\ 1\ <=\ 2^n
\end{equation*}
egyenlőtlenség teljesülése, hiszen n hosszú bináris vektorból
\begin{equation*}
2^n
\end{equation*}
darab van.
A mátrixot úgy alkottam meg, hogy a csupa nulla vektor és csupa egyes vektorokat ne használjam, ugyanis előbbi a hibátlan állapotot jelzi, utóbbi pedig minden másik vektorra VAGY-olva a csupa egyes vektort eredményezi, ezzel a feladat nem teljesülne.

Az egyenlőtlenség legkisebb pozitív egész megoldása a négy (lásd lenti kód).

In [ ]:
n = 4

nsqrd = n ** 2

print(f"n^2: {nsqrd}")

numofrows = n + 1

numofvectors = (((numofrows - 1) * (numofrows)) / 2) + numofrows

print(f"Vector count: {numofvectors}")

print(f"Required condition satisfied: {numofvectors <= nsqrd}")

### Mátrix előállítása
A szükséges feltétel segítségével megállapíthattuk, hogy legalább négy oszlopos mátrixra lesz szükségünk. Négy bit viszont a feladat többi feltételét is figyelembe véve nem elengendő.

Mivel a feladatban nem szerepel, hogy a legkisebb ilyen mátrixot kell megadni, ezért kezdetben hét oszloppal és nyolc sorral próbálkoztam ilyen mátrixot keresni. A mátrixot soronként készítettem el, minden sort úgy adtam hozzá a métrixomhoz, hogy a bitenkénti ```VAGY```-olással generált vektorok egyediek legyenek.

Így kaptam meg az alábbi mátrixot:

\begin{equation}
\begin{vmatrix}
1&0&0&0&0&1&0\\
0&1&0&0&1&0&0\\
0&0&1&1&0&0&0\\
0&0&1&0&0&1&0\\
1&0&0&0&0&0&1\\
0&1&1&0&0&0&0\\
1&0&0&0&1&0&0\\
0&0&0&1&0&0&1
\end{vmatrix}
\end{equation}

Ennek helyességét az alábbi Python kóddal ellenőriztem:

In [ ]:
!pip3 install -q numpy networkx matplotlib

In [ ]:
import numpy


mtx = \
[
          [1,0,0,0,0,1,0],
          [0,1,0,0,1,0,0],
          [0,0,1,1,0,0,0],
          [0,0,1,0,0,1,0],
          [1,0,0,0,0,0,1],
          [0,1,1,0,0,0,0],
          [1,0,0,0,1,0,0],
          [0,0,0,1,0,0,1]
]

vectors = [numpy.bitwise_or(mtx[i], mtx[j]) for i in range(len(mtx)) for j in range(i, len(mtx)) ]

n = 7
nsqrd = n ** 2
numofrows = n + 1
numofvectors = (((numofrows - 1) * (numofrows)) / 2) + numofrows

print(f"All generated vectors in the Matrix are unique: "
      f"{((len(vectors) == numofvectors) and (len(vectors) <= nsqrd)) and (len(vectors) == len(numpy.unique(vectors, axis=0)))}")

## Gráf előállítása
A mátrix elkészítése után láttam neki a az arra illeszkedő gráf elkészítésének. Egy olyan gráfot szerettem volna elkészíteni, aminek nyolc éle van és abban hét monitorozó út található.

A gráfh hibakódtáblájával bármely egy vagy két link meghibásodása detektálható, hiszen a mátrix bármely két sorának bitenkénti ```VAGY```-olása egyedi vektort eredményez.

A gráfhoz tartozó hibakódtábla:

\begin{array}{l|lllllll}
&t_1&t_2&t_3&t_4&t_5&t_6&t_7\\ \hline
A-B&1&0&0&0&0&1&0\\
C-D&0&1&0&0&1&0&0\\
D-B&0&0&1&1&0&0&0\\
E-D&0&0&1&0&0&1&0\\
A-D&1&0&0&0&0&0&1\\
C-E&0&1&1&0&0&0&0\\
A-B&1&0&0&0&1&0&0\\
E-F&0&0&0&1&0&0&1
\end{array}

A gráfot kirajzoló kód:

In [ ]:
import networkx

G = networkx.Graph()
G.add_edges_from([("A", "B"), ("A", "C"), ("A", "D"), ("C", "D"), ("B", "D"), ("D", "E"), ("C", "E"), ("E", "F")])

node_positions = {"A": (0., 1.), "B": (1., 1.), "C": (0., 0.), "D": (1., 0.), "E": (0.5, -1.3), "F": (1., -1.3)}

networkx.draw_networkx(G, pos=nx.rescale_layout_dict(node_positions), font_color="white")

edge_labels = \
{  
          ('A', 'B'): "1000010",
          ('A', 'D'): "1000001",
          ('C', 'A'): "1000100",
          ('C', 'D'): "0100100",
          ('D', 'B'): "0011000",
          ('D', 'E'): "0010010",
          ('C', 'E'): "0110000",
          ('E', 'F'): "0001001"
}
el = nx.draw_networkx_edge_labels(G, pos=nx.rescale_layout_dict(node_positions), edge_labels=edge_labels)